# Hybrid Matching

## Step 1: Prepare the Data

The data has already been preprocessed in the `data-preparation.ipynb` notebook. Now it needs to be loaded here and converted into the lookup dictionaries that will be used for the deterministic matching routine.

In [1]:
# Import the Pandas library for working with CSV data
import pandas as pd

# Read in the authors data
authors = pd.read_csv('../data/authors_db.csv',encoding='utf-8',quotechar='"')
# Read in the works data
works = pd.read_csv('../data/works_db.csv',encoding='utf-8',quotechar='"')

# Get basic information about the dataframes
authors.info()
works.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 27290 entries, 0 to 27289
Data columns (total 3 columns):
 #   Column                   Non-Null Count  Dtype 
---  ------                   --------------  ----- 
 0   Variant                  27290 non-null  object
 1   Authorized Name          27290 non-null  object
 2   DLL Identifier (Author)  27290 non-null  object
dtypes: object(3)
memory usage: 639.7+ KB
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5315 entries, 0 to 5314
Data columns (total 3 columns):
 #   Column                   Non-Null Count  Dtype 
---  ------                   --------------  ----- 
 0   Title                    5315 non-null   object
 1   DLL Identifier (Work)    5315 non-null   object
 2   DLL Identifier (Author)  5315 non-null   object
dtypes: object(3)
memory usage: 124.7+ KB


In [2]:
# Change the names of the columns to be lower case without spaces or punctuation
authors = authors.rename(columns={'Variant':'variant_name','Authorized Name':'authorized_name','DLL Identifier (Author)':'dll_id_author'})
works = works.rename(columns={'Title':'title','DLL Identifier (Work)':'dll_id_work','DLL Identifier (Author)': 'dll_id_author'})

In [3]:
# Import the utility functions for making dictionaries
import utilities as utilities

# Prepare the lookup dictionaries of variant author names and titles
variant_to_authorized, title_to_work = utilities.prepare_dicts(authors,works)


In [4]:
# Prepare the dictionaries for embedding the author names and titles
canonical_authors = authors.to_dict("records")
canonical_titles = works.to_dict("records")

## Load the Vector Stores

See `vector_stores.ipynb`.

In [5]:
# Code for loading vector stores, if needed
import faiss
import pickle

author_index = faiss.read_index("../author_index.faiss")
title_index = faiss.read_index("../title_index.faiss")

with open("../author_map.pkl", "rb") as f:
    author_map = pickle.load(f)

with open("../title_map.pkl", "rb") as f:
    title_map = pickle.load(f)

## Load the Models

### Load the DistilBERT author matching model

In [6]:
from transformers import AutoTokenizer, AutoModelForSequenceClassification

# Path to your saved fine-tuned model
distilbert_model_path = '../distilbert-finetuned'

# Load the tokenizer and model
distilbert_tokenizer = AutoTokenizer.from_pretrained(distilbert_model_path)
distilbert_model = AutoModelForSequenceClassification.from_pretrained(distilbert_model_path)

# Verify label mappings
label2id = distilbert_model.config.label2id
id2label = distilbert_model.config.id2label

print("Label-to-ID Mapping:", label2id)
print("ID-to-Label Mapping:", id2label)

Label-to-ID Mapping: {'A1868': 1960, 'A1870': 2246, 'A2181': 2618, 'A2491': 14, 'A2492': 2290, 'A2493': 2215, 'A2494': 1752, 'A2495': 1554, 'A2508': 2051, 'A2755': 152, 'A2868': 365, 'A2870': 2274, 'A2871': 2455, 'A2872': 2372, 'A2873': 2917, 'A2874': 2558, 'A2875': 2821, 'A2876': 2690, 'A2877': 2536, 'A2878': 2419, 'A2879': 1455, 'A2880': 3074, 'A2881': 2952, 'A2882': 2626, 'A2883': 91, 'A2884': 2846, 'A2885': 1127, 'A2886': 2669, 'A2887': 1630, 'A2888': 733, 'A2889': 2798, 'A2890': 2396, 'A2891': 465, 'A2892': 2437, 'A2893': 3078, 'A2894': 2814, 'A2895': 2550, 'A2896': 1013, 'A2897': 498, 'A2898': 3053, 'A2901': 2435, 'A2902': 2147, 'A2903': 1443, 'A2904': 2325, 'A2905': 2570, 'A2906': 2606, 'A2907': 1235, 'A2908': 1622, 'A2909': 1236, 'A2910': 765, 'A2911': 330, 'A2912': 3049, 'A2913': 2385, 'A2914': 3077, 'A2915': 764, 'A2916': 2894, 'A2917': 2795, 'A2918': 2788, 'A2919': 2465, 'A2920': 127, 'A2921': 1530, 'A2922': 2941, 'A2923': 1462, 'A2924': 1205, 'A2925': 3086, 'A2926': 2773, '

### Load the Greek-Latin Classification 

It turns out that a lot of the values in the `author` column are Greek names. That's because the titles of critical editions of Greek texts are often published with Latinized forms of the authors' names and titles. That actually makes the results a little better.

**Conclusion** I should remove the Greek authors before doing any analysis.

Fortunately, I have a list of Greek author names that I pulled from the TLG and the Perseus Project. I tried to use those to reduce the number of records in the dataframe, but there were problems with that approach. First, the file had some mislabeled names in it. Second, it didn't match all the Greek names, since it didn't have enough variant name forms to be effective.

After trying various other things, I decided to train a model to identify Greek and Latin authors (see `python/fine_tune_distilmbert_greek.ipynb` and `greek-data-prep.ipynb` for more on that process). Now that I have that model trained, I'll use it to separate the Greek authors from the Latin authors.

In [7]:
from transformers import DistilBertForSequenceClassification, DistilBertTokenizerFast
# Ensure labels are loaded
greek_model_path = '../greek'
greek_model = DistilBertForSequenceClassification.from_pretrained(greek_model_path)
greek_tokenizer = DistilBertTokenizerFast.from_pretrained(greek_model_path)

# Uncomment this code if the labels are `LABEL_1`, etc.
#
# if not hasattr(greek_model.config, "id2label") or not greek_model.config.id2label:
#     # Define your labels if they weren't saved correctly
#     labels = ["Latin", "Greek"]
#     greek_model.config.id2label = {idx: label for idx, label in enumerate(labels)}
#     greek_model.config.label2id = {label: idx for idx, label in enumerate(labels)}

# greek_model.config.id2label = {0: "Greek", 1: "Latin"}
# greek_model.config.label2id = {"Greek": 0, "Latin": 1}

# # Save the updated model configuration
# greek_model.save_pretrained('../greek')
# Verify label mappings
label2id = greek_model.config.label2id
id2label = greek_model.config.id2label

print("Label-to-ID Mapping:", label2id)
print("ID-to-Label Mapping:", id2label)

Label-to-ID Mapping: {'Greek': 0, 'Latin': 1}
ID-to-Label Mapping: {0: 'Greek', 1: 'Latin'}


## Import LatinCy (Spacy)

I'm using [LatinCy](https://huggingface.co/latincy) to parse titles in the incoming metadata. Below, in the utility functions, I tokenize the words in the title, then lemmatize them and look for matches between the lemmatized words and the lemmatized canonical titles in the DLL Catalog's work records.

In [8]:
# Import LatinCy for parsing title strings
import spacy

# Load the LatinCy spaCy model
try:
    nlp = spacy.load('la_core_web_lg')
except OSError:
    print("Downloading LatinCy model...")
    from spacy.cli import download
    download("")
    nlp = spacy.load('la_core_web_lg')

from spacy.lang.la import STOP_WORDS

# Augment the Latin stop words list
custom_stop_words = {"liber", "libri", "libro", "librum", "librorum", "libris", "libros"}
all_stop_words = STOP_WORDS.union(custom_stop_words)

## Utility Functions

In [9]:
from rapidfuzz import fuzz, process
import torch
import torch.nn.functional as F
import unicodedata
import re
# Note: some helper functions are in `utilities.py`, which was imported above.

# Step 1: Language Classification Functions
def classify_author_language(input_author):
    """Classify the author's language as Greek or Latin using the fine-tuned model."""
    if not isinstance(input_author, str):
        return "Unknown", 0.0

    # Tokenize and encode the input author name
    inputs = greek_tokenizer(input_author, return_tensors="pt", truncation=True, padding=True)
    outputs = greek_model(**inputs)
    logits = outputs.logits.detach().cpu()

    # Apply softmax to logits to get probabilities
    probabilities = F.softmax(logits, dim=-1).numpy()
    predicted_class = probabilities.argmax(axis=-1)[0]
    confidence = probabilities.max()  # Highest probability

    # Use the id2label mapping for label names
    predicted_label = greek_model.config.id2label[predicted_class]
    print(f"Language Classification: {input_author} -> {predicted_label} (Confidence: {confidence:.4f})")

    return predicted_label, confidence

def classify_and_split_by_language(processed_df):
    """Classify authors as Greek or Latin, add language info, and split the dataframe."""
    language_results = []

    for _, row in processed_df.iterrows():
        input_author = row["author"]

        # Perform language classification
        author_language, language_confidence = classify_author_language(input_author)

        # Add the results to a new row while preserving existing data
        updated_row = {
            **row,  # Include all original columns
            "language": author_language,
            "language_confidence": language_confidence,
        }
        language_results.append(updated_row)

    # Create a dataframe with the updated rows
    classified_df = pd.DataFrame(language_results)

    # Split the dataframe into Greek and Latin subsets
    greek_df = classified_df[classified_df["language"] == "Greek"].reset_index(drop=True)
    latin_df = classified_df[classified_df["language"] == "Latin"].reset_index(drop=True)

    return classified_df, greek_df, latin_df

# Step 2: Author Matching Functions
def deterministic_author_match(input_author):
    input_author_decomposed = unicodedata.normalize('NFKD', input_author).encode('ascii', 'ignore').decode('utf-8')
    input_author_no_punct = re.sub(r'[^\w\s]', '', input_author_decomposed)
    input_author_cleaned = input_author_no_punct.lower().strip()
    author_info = variant_to_authorized.get(input_author_cleaned)
    return author_info

def fuzzy_author_match(input_author):
    input_author_cleaned = utilities.normalize_author_name(input_author)
    result = process.extractOne(input_author_cleaned, list(variant_to_authorized.keys()), scorer=fuzz.WRatio)
    if result:
        best_match, similarity, *_ = result
        if similarity > 90:
            return variant_to_authorized.get(best_match), similarity / 100
    return None, 0.0

def distilbert_author_match(input_author):
    if not isinstance(input_author, str):
        return None, 0.0

    inputs = distilbert_tokenizer(input_author, return_tensors="pt", truncation=True, padding=True)
    outputs = distilbert_model(**inputs)
    logits = outputs.logits
    predicted_class = torch.argmax(logits, dim=-1).item()
    confidence = torch.softmax(logits, dim=-1).max().item()

    predicted_author_id = distilbert_model.config.id2label[predicted_class]
    for variant, author_info in variant_to_authorized.items():
        if author_info["author_id"] == predicted_author_id:
            return author_info, confidence
    return None, 0.0

# Step 3: Title Matching Functions
def tokenize_title(title):
    doc = nlp(title.lower().strip())
    tokens = [
        token.lemma_ if token.lemma_ not in {"aeneidus", "aeneus"} else "aeneis"
        for token in doc
        if token.is_alpha and token.lemma_ not in all_stop_words
    ]
    return tokens

def deterministic_title_match(input_title, author_id):
    """Match title using deterministic lookups or tokenized search, filtered by author_id."""
    if not author_id:
        return None  # Skip matching if no author_id is provided

    input_title_cleaned = input_title.lower().strip()

    # Filter titles by author_id
    filtered_titles = {key: value for key, value in title_to_work.items() if value["dll_id_author"] == author_id}

    # Direct deterministic match
    title_info = filtered_titles.get(input_title_cleaned)
    if title_info:
        title_info["title"] = input_title_cleaned  # Explicitly set the title key
        print(f"Deterministic title match: {title_info}")
        return title_info

    # Tokenized search
    input_tokens = tokenize_title(input_title)
    for token in input_tokens:
        if token in filtered_titles:
            title_info = filtered_titles[token]
            title_info["title"] = token  # Explicitly set the title key
            print(f"Tokenized title match: {title_info}")
            return title_info

    return None

def fuzzy_title_match(input_title, author_id):
    """Fuzzy match input_title against titles filtered by author_id."""
    if not author_id:
        return None, 0.0  # Skip matching if no author_id is provided

    # Filter titles by author_id
    filtered_titles = {key: value for key, value in title_to_work.items() if value["dll_id_author"] == author_id}

    if not filtered_titles:
        return None, 0.0  # No titles available for matching

    # Perform fuzzy matching
    result = process.extractOne(
        input_title,
        list(filtered_titles.keys()),
        scorer=fuzz.WRatio
    )

    if result:
        best_match, score, *_ = result  # Unpack necessary values
        if score > 85:  # Confidence threshold for fuzzy matching
            print(f"Fuzzy title match: {best_match} with score {score}")
            title_info = filtered_titles[best_match]
            title_info["title"] = best_match
            return title_info, score / 100
    return None, 0.0


In [10]:
def process_metadata(input_df):
    """Process input dataframe and match metadata."""
    results = []

    for _, row in input_df.iterrows():
        input_author_original = row["author"]
        input_author_normalized = utilities.normalize_author_name(input_author_original)
        input_title = row["title"]
        print(f'Processing: {input_author_original}')

        # Author Matching
        deterministic_author = deterministic_author_match(input_author_normalized)
        fuzzy_author, fuzzy_author_score = fuzzy_author_match(input_author_normalized)
        distilbert_author, distilbert_author_score = distilbert_author_match(input_author_original)

        # Choose the author_id to use for title matching
        author_id_for_title_matching = None
        if deterministic_author:
            author_id_for_title_matching = deterministic_author["author_id"]
        elif distilbert_author:
            author_id_for_title_matching = distilbert_author["author_id"]
        
        # Title Matching (filtered by matched author_id)
        deterministic_title_info = deterministic_title_match(input_title, author_id_for_title_matching)
        fuzzy_title_info, fuzzy_title_score = fuzzy_title_match(input_title, author_id_for_title_matching)

        # Extract the matched title (if available)
        matched_title_deterministic = deterministic_title_info["title"] if deterministic_title_info else "Unknown"
        matched_title_fuzzy = fuzzy_title_info["title"] if fuzzy_title_info else "Unknown"

        # Collect Results
        results.append({
            "author": input_author_original,
            "deterministic_author": deterministic_author,
            "fuzzy_author": fuzzy_author,
            "fuzzy_author_score": fuzzy_author_score,
            "distilbert_author": distilbert_author,
            "distilbert_author_score": distilbert_author_score,
            "title": input_title,
            "matched_title_deterministic": matched_title_deterministic,
            "matched_title_fuzzy": matched_title_fuzzy,
            "fuzzy_title_score": fuzzy_title_score,
        })
        print(f"Matched author: {deterministic_author if deterministic_author else distilbert_author}")

    return pd.DataFrame(results)


In [11]:
import csv

from codecarbon import EmissionsTracker

# Setup CodeCarbon's EmissionsTracker
tracker = EmissionsTracker()
tracker.start()

def clean_input(df):
    """Ensure all author and title values are strings, replacing NaN with 'Unknown'."""
    df["author"] = df["author"].fillna("Unknown").astype(str)
    df["title"] = df["title"].fillna("Unknown").astype(str)
    return df

# Apply cleaning before processing metadata
input_df = pd.read_csv('../data/hathi.csv', encoding='utf-8', quotechar='"')
input_df = clean_input(input_df)  # Clean the data
print('Classifying authors as Greek or Latin …')
classified_df, greek_df, latin_df = classify_and_split_by_language(input_df)
# Save the results if needed
classified_df.to_csv("../data/classified_metadata.csv", index=False, encoding='utf-8', quoting=csv.QUOTE_ALL)
greek_df.to_csv("../data/greek_authors.csv", index=False, encoding='utf-8', quoting=csv.QUOTE_ALL)
latin_df.to_csv("../data/latin_authors.csv", index=False, encoding='utf-8', quoting=csv.QUOTE_ALL)
print("Done with classification. Beginning to process authors and titles.")
output_df = process_metadata(latin_df)
print("Done with processing authors and titles.")
display(output_df.head())
output_df.to_csv('../data/output_df.csv',index=False, encoding='utf-8', quoting=csv.QUOTE_ALL)

# Stop the emissions tracker after training is complete
emissions = tracker.stop()

print(f"Estimated CO2 emissions for training: {emissions} kg")


[codecarbon INFO @ 10:48:01] [setup] RAM Tracking...
[codecarbon INFO @ 10:48:01] [setup] GPU Tracking...
[codecarbon INFO @ 10:48:01] No GPU found.
[codecarbon INFO @ 10:48:01] [setup] CPU Tracking...
[codecarbon WARNING @ 10:48:01] No CPU tracking mode found. Falling back on CPU constant mode.
[codecarbon INFO @ 10:48:02] CPU Model on constant consumption mode: Intel(R) Core(TM) i7-9750H CPU @ 2.60GHz
[codecarbon INFO @ 10:48:02] >>> Tracker's metadata:
[codecarbon INFO @ 10:48:02]   Platform system: macOS-10.16-x86_64-i386-64bit
[codecarbon INFO @ 10:48:02]   Python version: 3.10.15
[codecarbon INFO @ 10:48:02]   CodeCarbon version: 2.2.2
[codecarbon INFO @ 10:48:02]   Available RAM : 16.000 GB
[codecarbon INFO @ 10:48:02]   CPU count: 12
[codecarbon INFO @ 10:48:02]   CPU model: Intel(R) Core(TM) i7-9750H CPU @ 2.60GHz
[codecarbon INFO @ 10:48:02]   GPU count: None
[codecarbon INFO @ 10:48:02]   GPU model: None


Classifying authors as Greek or Latin …
Language Classification: Du Creux, François, 1596?-1666. -> Latin (Confidence: 1.0000)
Language Classification: Meyer, Ernst H. F. 1791-1858. -> Latin (Confidence: 1.0000)
Language Classification: Laet, Joannes de, 1593-1649. -> Latin (Confidence: 1.0000)
Language Classification: Caesar, Julius -> Latin (Confidence: 1.0000)
Language Classification: Unknown -> Latin (Confidence: 1.0000)
Language Classification: Drexel, Jeremias, 1581-1638, -> Latin (Confidence: 1.0000)
Language Classification: Kircher, Athanasius, 1602-1680 -> Latin (Confidence: 1.0000)
Language Classification: Drexel, Jeremias, 1581-1638, -> Latin (Confidence: 1.0000)
Language Classification: Drexel, Jeremias, 1581-1638, -> Latin (Confidence: 1.0000)
Language Classification: Drexel, Jeremias, 1581-1638, -> Latin (Confidence: 1.0000)
Language Classification: Drexel, Jeremias, 1581-1638, -> Latin (Confidence: 1.0000)
Language Classification: Hincmar, Archbishop of Reims, approximat

[codecarbon INFO @ 10:48:21] Energy consumed for RAM : 0.000025 kWh. RAM Power : 6.0 W
[codecarbon INFO @ 10:48:21] Energy consumed for all CPUs : 0.000094 kWh. Total CPU Power : 22.5 W
[codecarbon INFO @ 10:48:21] 0.000119 kWh of electricity used since the beginning.


Language Classification: Horace -> Latin (Confidence: 1.0000)
Language Classification: Horace. -> Latin (Confidence: 1.0000)
Language Classification: Horace -> Latin (Confidence: 1.0000)
Language Classification: Horace. -> Latin (Confidence: 1.0000)
Language Classification: Livy -> Latin (Confidence: 1.0000)
Language Classification: Livy -> Latin (Confidence: 1.0000)
Language Classification: Livy -> Latin (Confidence: 1.0000)
Language Classification: Livy -> Latin (Confidence: 1.0000)
Language Classification: Livy -> Latin (Confidence: 1.0000)
Language Classification: Livy -> Latin (Confidence: 1.0000)
Language Classification: Livy -> Latin (Confidence: 1.0000)
Language Classification: Livy -> Latin (Confidence: 1.0000)
Language Classification: Livy -> Latin (Confidence: 1.0000)
Language Classification: Livy -> Latin (Confidence: 1.0000)
Language Classification: Livy -> Latin (Confidence: 1.0000)
Language Classification: Livy -> Latin (Confidence: 1.0000)
Language Classification: Livy 

[codecarbon INFO @ 10:48:36] Energy consumed for RAM : 0.000050 kWh. RAM Power : 6.0 W
[codecarbon INFO @ 10:48:36] Energy consumed for all CPUs : 0.000188 kWh. Total CPU Power : 22.5 W
[codecarbon INFO @ 10:48:36] 0.000238 kWh of electricity used since the beginning.


...

[codecarbon INFO @ 12:29:09] Energy consumed for RAM : 0.010103 kWh. RAM Power : 6.0 W
[codecarbon INFO @ 12:29:09] Energy consumed for all CPUs : 0.037890 kWh. Total CPU Power : 22.5 W
[codecarbon INFO @ 12:29:09] 0.047993 kWh of electricity used since the beginning.


Matched author: {'authorized_name': 'linné, carl von, 1707-1778', 'author_id': 'A5601'}
Processing: Thomas, Aquinas, Saint, 1225?-1274.
Fuzzy title match: sermo 'petite et accipietis' with score 85.5
Matched author: {'authorized_name': 'thomas, aquinas, saint', 'author_id': 'A4997'}
Processing: Thomas, Aquinas, Saint, 1225?-1274.
Fuzzy title match: sermo 'petite et accipietis' with score 85.5
Matched author: {'authorized_name': 'thomas, aquinas, saint', 'author_id': 'A4997'}
Processing: Thomas, Aquinas, Saint, 1225?-1274.
Fuzzy title match: sermo 'petite et accipietis' with score 85.5
Matched author: {'authorized_name': 'thomas, aquinas, saint', 'author_id': 'A4997'}
Processing: Thomas, Aquinas, Saint, 1225?-1274.
Fuzzy title match: sermo 'petite et accipietis' with score 85.5
Matched author: {'authorized_name': 'thomas, aquinas, saint', 'author_id': 'A4997'}
Processing: Thomas, Aquinas, Saint, 1225?-1274.
Fuzzy title match: sermo 'petite et accipietis' with score 85.5
Matched author:

author deterministic_author  \
0  Du Creux, François, 1596?-1666.                 None   
1    Meyer, Ernst H. F. 1791-1858.                 None   
2     Laet, Joannes de, 1593-1649.                 None   
3                   Caesar, Julius                 None   
4                          Unknown                 None   

                                        fuzzy_author  fuzzy_author_score  \
0                                               None                0.00   
1                                               None                0.00   
2                                               None                0.00   
3  {'authorized_name': 'caesar, julius', 'author_...                0.96   
4                                               None                0.00   

                                   distilbert_author  distilbert_author_score  \
0  {'authorized_name': 'cruz, luís da, 1543-1604...                 0.467436   
1  {'authorized_name': 'meyer, wilhelm, 1845-1917...                 0.999939   
2  {'authorized_name': 'larroumet, gustave', 'aut...                 0.494394   
3  {'authorized_name': 'caesar, julius', 'author_...                 0.999999   
4  {'authorized_name': 'stephanus abbas 4. or 6th...                 0.177454   

                                               title  \
0  Historiæ canadensis, seu Novæ-Franciæ libri de...   
1  Ernesti Meyer de plantis labradoricis libri tres.   
2  Novus orbis, seu Descriptionis Indiae Occident...   
3  C. Julii Cæsaris commentariorum De Bello Galli...   
4  Collectanea latina seu ecclesiasticæ antiquita...   

  matched_title_deterministic matched_title_fuzzy  fuzzy_title_score  
0                     Unknown             Unknown                0.0  
1                     Unknown             Unknown                0.0  
2                     Unknown             Unknown                0.0  
3                     Unknown             Unknown                0.0  
4                     Unknown             Unknown                0.0

[codecarbon INFO @ 12:29:21] Energy consumed for RAM : 0.010122 kWh. RAM Power : 6.0 W
[codecarbon INFO @ 12:29:21] Energy consumed for all CPUs : 0.037962 kWh. Total CPU Power : 22.5 W
[codecarbon INFO @ 12:29:21] 0.048084 kWh of electricity used since the beginning.


Estimated CO2 emissions for training: 0.022890762940307632 kg


That ran in 101 mins 19.9 secs.

In [12]:
print(f"Number of rows in the Greek dataframe: {len(greek_df)}")
print(f"Number of rows in the Latin dataframe: {len(latin_df)}")

print(f"The classification step removed {len(classified_df)-len(latin_df)} records.")

Number of rows in the Greek dataframe: 2828
Number of rows in the Latin dataframe: 21971
The classification step removed 2828 records.


In [13]:
for author in greek_df['author'].unique():
    print(author)

Arrian.
Euclid,
Herodotus.
Celsus, Aulus Cornelius.
Anacreon
John Chrysostom, Saint, -407
Clement, of Alexandria, Saint, approximately 150-approximately 215
Herodotus
Nemesius, Bp. of Emesa
Pindar
Theocritus.
Xenophon
Frontinus, Sextus Julius
Catherine, of Alexandria, Saint.
Aristophanes.
Index librorum prohibitorum.
Homer
Epiphanius, Saint, Bishop of Constantia in Cyprus, approximately 310-403.
Euripides
Philo, of Alexandria
Plato.
Plato
Plotinus
Demosthenes
Plutarch.
Homer.
Theophrastus.
Thucydides
Epictetus
Origen
Celsus, Aulus Cornelius
Epiphanius, Saint, Bishop of Constantia in Cyprus, approximately 310-403
Aristotle
Archimedes.
Dioscorides Pedanius, of Anazarbos
Nicomachus, of Gerasa.
Proclus, approximately 410-485
Xenophon, of Ephesus
Gregory, of Nyssa, Saint, approximately 335-approximately 394.
Theocritus
Sextus, Empiricus
Philostratus, the Athenian, active 2nd century-3rd century
Longus
Stobaeus
Apollonius, of Athens.
Arrian
Frontinus, Sextus Julius.
Philo, of Byzantium
Justi

Those results look pretty solid.

In [16]:
# Apply cleaning before processing metadata
input_df = pd.read_csv('../data/unknown_title_known_authors.csv', encoding='utf-8', quotechar='"')
input_df = clean_input(input_df)  # Clean the data
print('Classifying authors as Greek or Latin …')
classified_df, greek_df, latin_df = classify_and_split_by_language(input_df)

Classifying authors as Greek or Latin …
Language Classification: Caesar, Julius -> Latin (Confidence: 1.0000)
Language Classification: Kircher, Athanasius, 1602-1680 -> Latin (Confidence: 1.0000)
Language Classification: Hincmar, Archbishop of Reims, approximately 806-882 -> Latin (Confidence: 1.0000)
Language Classification: Acosta, José de, 1540-1600, -> Latin (Confidence: 1.0000)
Language Classification: Hincmar, Archbishop of Reims, approximately 806-882 -> Latin (Confidence: 1.0000)
Language Classification: Hincmar, Archbishop of Reims, approximately 806-882 -> Latin (Confidence: 1.0000)
Language Classification: Kircher, Athanasius, 1602-1680. -> Latin (Confidence: 1.0000)
Language Classification: Mersenne, Marin, 1588-1648, -> Latin (Confidence: 1.0000)
Language Classification: Hincmar, Archbishop of Reims, approximately 806-882 -> Latin (Confidence: 1.0000)
Language Classification: Kircher, Athanasius, 1602-1680. -> Latin (Confidence: 1.0000)
Language Classification: Virgil. ->

In [17]:
# Save the results if needed
classified_df.to_csv("../data/unknown_title_known_author_classified_metadata.csv", index=False, encoding='utf-8', quoting=csv.QUOTE_ALL)
greek_df.to_csv("../data/unknown_title_known_author_greek_authors.csv", index=False, encoding='utf-8', quoting=csv.QUOTE_ALL)
latin_df.to_csv("../data/unknown_title_known_author_latin_authors.csv", index=False, encoding='utf-8', quoting=csv.QUOTE_ALL)

In [22]:
# Change the fuzzy matching algorithm to partial_token_set_ratio
def fuzzy_title_match(input_title, author_id):
    """Fuzzy match input_title against titles filtered by author_id."""
    if not author_id:
        return None, 0.0  # Skip matching if no author_id is provided

    # Filter titles by author_id
    filtered_titles = {key: value for key, value in title_to_work.items() if value["dll_id_author"] == author_id}

    if not filtered_titles:
        return None, 0.0  # No titles available for matching

    # Perform fuzzy matching
    result = process.extractOne(
        input_title,
        list(filtered_titles.keys()),
        scorer=fuzz.partial_token_set_ratio
    )

    if result:
        best_match, score, *_ = result  # Unpack necessary values
        if score > 85:  # Confidence threshold for fuzzy matching
            print(f"Fuzzy title match: {best_match} with score {score}")
            title_info = filtered_titles[best_match]
            title_info["title"] = best_match
            return title_info, score / 100
    return None, 0.0


In [23]:
output_df = process_metadata(latin_df)
print("Done with processing authors and titles.")
display(output_df.head())
output_df.to_csv('../data/unknown_title_known_author_output.csv',index=False, encoding='utf-8', quoting=csv.QUOTE_ALL)

Processing: Caesar, Julius
Matched author: {'authorized_name': 'caesar, julius', 'author_id': 'A4644'}
Processing: Kircher, Athanasius, 1602-1680
Matched author: {'authorized_name': 'kircher, athanasius, 1602-1680', 'author_id': 'A4106'}
Processing: Hincmar, Archbishop of Reims, approximately 806-882
Matched author: {'authorized_name': 'hincmar, archbishop of reims', 'author_id': 'A5135'}
Processing: Acosta, José de, 1540-1600,
Matched author: {'authorized_name': 'acosta, josé de, 1540-1600', 'author_id': 'A5598'}
Processing: Hincmar, Archbishop of Reims, approximately 806-882
Matched author: {'authorized_name': 'hincmar, archbishop of reims', 'author_id': 'A5135'}
Processing: Hincmar, Archbishop of Reims, approximately 806-882
Matched author: {'authorized_name': 'hincmar, archbishop of reims', 'author_id': 'A5135'}
Processing: Kircher, Athanasius, 1602-1680.
Matched author: {'authorized_name': 'kircher, athanasius, 1602-1680', 'author_id': 'A4106'}
Processing: Mersenne, Marin, 1588-

author  \
0                                     Caesar, Julius   
1                     Kircher, Athanasius, 1602-1680   
2  Hincmar, Archbishop of Reims, approximately 80...   
3                       Acosta, José de, 1540-1600,   
4  Hincmar, Archbishop of Reims, approximately 80...   

                                deterministic_author  \
0                                               None   
1  {'authorized_name': 'kircher, athanasius, 1602...   
2                                               None   
3  {'authorized_name': 'acosta, josé de, 1540-16...   
4                                               None   

                                        fuzzy_author  fuzzy_author_score  \
0  {'authorized_name': 'caesar, julius', 'author_...            0.960000   
1  {'authorized_name': 'kircher, athanasius, 1602...            1.000000   
2  {'authorized_name': 'hincmar, archbishop of re...            0.909859   
3  {'authorized_name': 'acosta, josé de, 1540-16...            1.000000   
4  {'authorized_name': 'hincmar, archbishop of re...            0.909859   

                                   distilbert_author  distilbert_author_score  \
0  {'authorized_name': 'caesar, julius', 'author_...                 0.999999   
1  {'authorized_name': 'kircher, athanasius, 1602...                 1.000000   
2  {'authorized_name': 'hincmar, archbishop of re...                 0.999999   
3  {'authorized_name': 'acosta, josé de, 1540-16...                 1.000000   
4  {'authorized_name': 'hincmar, archbishop of re...                 0.999999   

                                               title  \
0  C. Julii Cæsaris commentariorum De Bello Galli...   
1  Athanasii Kircheri e Soc. Jesu mundus subterra...   
2  Hincmari archiepiscopi Remensis opera : duos i...   
3  Iosephi A Costa, Societatis Iesu, De natura no...   
4  Hincmari archiepiscopi Remensis opera : duos i...   

  matched_title_deterministic matched_title_fuzzy  fuzzy_title_score  
0                     Unknown             Unknown                0.0  
1                     Unknown             Unknown                0.0  
2                     Unknown             Unknown                0.0  
3                     Unknown             Unknown                0.0  
4                     Unknown             Unknown                0.0

In [20]:
output_df

author  \
0                                        Caesar, Julius   
1                        Kircher, Athanasius, 1602-1680   
2     Hincmar, Archbishop of Reims, approximately 80...   
3                          Acosta, José de, 1540-1600,   
4     Hincmar, Archbishop of Reims, approximately 80...   
...                                                 ...   
7606                                              Livy.   
7607                                      Lucan, 39-65.   
7608                                Tacitus, Cornelius.   
7609                        Linné, Carl von, 1707-1778   
7610                                           Persius.   

                                   deterministic_author  \
0                                                  None   
1     {'authorized_name': 'kircher, athanasius, 1602...   
2                                                  None   
3     {'authorized_name': 'acosta, josé de, 1540-16...   
4                                                  None   
...                                                 ...   
7606  {'authorized_name': 'livy', 'author_id': 'A4979'}   
7607  {'authorized_name': 'lucan', 'author_id': 'A50...   
7608  {'authorized_name': 'tacitus, cornelius', 'aut...   
7609  {'authorized_name': 'linné, carl von, 1707-17...   
7610  {'authorized_name': 'persius', 'author_id': 'A...   

                                           fuzzy_author  fuzzy_author_score  \
0     {'authorized_name': 'caesar, julius', 'author_...            0.960000   
1     {'authorized_name': 'kircher, athanasius, 1602...            1.000000   
2     {'authorized_name': 'hincmar, archbishop of re...            0.909859   
3     {'authorized_name': 'acosta, josé de, 1540-16...            1.000000   
4     {'authorized_name': 'hincmar, archbishop of re...            0.909859   
...                                                 ...                 ...   
7606  {'authorized_name': 'livy', 'author_id': 'A4979'}            1.000000   
7607  {'authorized_name': 'lucan', 'author_id': 'A50...            1.000000   
7608  {'authorized_name': 'tacitus, cornelius', 'aut...            1.000000   
7609  {'authorized_name': 'linné, carl von, 1707-17...            1.000000   
7610  {'authorized_name': 'persius', 'author_id': 'A...            1.000000   

                                      distilbert_author  \
0     {'authorized_name': 'caesar, julius', 'author_...   
1     {'authorized_name': 'kircher, athanasius, 1602...   
2     {'authorized_name': 'hincmar, archbishop of re...   
3     {'authorized_name': 'acosta, josé de, 1540-16...   
4     {'authorized_name': 'hincmar, archbishop of re...   
...                                                 ...   
7606  {'authorized_name': 'livy', 'author_id': 'A4979'}   
7607  {'authorized_name': 'lucan', 'author_id': 'A50...   
7608  {'authorized_name': 'tacitus, cornelius', 'aut...   
7609  {'authorized_name': 'linné, carl von, 1707-17...   
7610  {'authorized_name': 'persius', 'author_id': 'A...   

      distilbert_author_score  \
0                    0.999999   
1                    1.000000   
2                    0.999999   
3                    1.000000   
4                    0.999999   
...                       ...   
7606                 1.000000   
7607                 0.999998   
7608                 1.000000   
7609                 0.999995   
7610                 1.000000   

                                                  title  \
0     C. Julii Cæsaris commentariorum De Bello Galli...   
1     Athanasii Kircheri e Soc. Jesu mundus subterra...   
2     Hincmari archiepiscopi Remensis opera : duos i...   
3     Iosephi A Costa, Societatis Iesu, De natura no...   
4     Hincmari archiepiscopi Remensis opera : duos i...   
...                                                 ...   
7606  Il libro II delle storie / di Tito Livio ; com...   
7607  De bello civili : liber VII / M. Annaei Lucani...   
7608  Historiarum libri qui supersunt / Corne